In [1]:
import numpy as np

In [2]:
# Paths
path_dataset_1 = "../data/2021_02_01_neurovascular_datasets/"
path_dataset_1_neuro = f"{path_dataset_1}/2021_02_01_18_45_51_mouse_flipped_channels__1_FOV3_6100um_deep_512l_3x_mag_1850_sec_acq_with_FLIM_4Mcps_laser_pulses_with_TAG_00031_neuronal_longitudinal__dff.zarr"
path_dataset_1_vascular = f"{path_dataset_1}/2021_02_01_18_45_51_mouse_flipped_channels__1_FOV3_6100um_deep_512l_3x_mag_1850_sec_acq_with_FLIM_4Mcps_laser_pulses_with_TAG_00031_vascular_2.5_Hz_lpf_radon_longitudinal_.zarr"

# TODO load and explore coordinates data

In [3]:
# make sure you `pip install zarr`

# Load data from `zarr` files
import zarr

data_1_neuro = zarr.load(path_dataset_1_neuro)
data_1_vascu = zarr.load(path_dataset_1_vascular)

In [4]:
# :Lior's Explanation:
# From the neuronal zarr they should fetch the 'neuronal_dff' dataset, 
# and possibly the 'imaging_rate' and 'time_vector' datasets (if they want). 

# From the vascular zarr they should fetch the 'time_varying_vascular_diameter' dataset
# if they look for Radon-based diameter estimations, or 'branching_vessel_photon_count, 
# if they prefer to watch how many photons were counted in each vessel segment (corrected for
# axial variations in dwell time). They might also want to use the 'vascular_angle' extracted for
# each vessel segment.
# The same zip file also contains a TIF file with the time-collapsed vascular volume, rescaled to
# 1 voxel per cubic micron.

In [11]:
# Loading Neuro Features:
neuronal_dff = data_1_neuro.get("neuronal_dff")  # neurons activity
time_vector = data_1_neuro.get("time_vector")

imaging_rate = data_1_neuro.get("imaging_rate")

print(f"neuronal_dff.shape={neuronal_dff.shape}")
print(f"time_vector.shape={time_vector.shape}")
print(f"imaging_rate={imaging_rate}")

neuronal_dff.shape=(50, 3028)
time_vector.shape=(3028,)
imaging_rate=30.02


In [18]:
# Plotting some graphs of neural-activity
import plotly.express as px
from scipy.signal import savgol_filter

x, y = time_vector, neuronal_dff[0]

px.scatter(x=x, y=y, title="Neuron by Time").show()

yhat = savgol_filter(y, 51, 3) # window size 51, polynomial order 3
px.scatter(x=x, y=yhat, title="Neuron by Time [Smoothed]", color_discrete_sequence=["orange"]).show()


print_neuro_values_dist(limit=5)

Values Dist for each Neuronl


In [19]:
# Loading Vascular Features:
vascular_diameter = data_1_vascu.get("time_varying_vascular_diameter").T

print(f"vascular_diameter.shape={vascular_diameter.shape}")

vascular_diameter.shape=(426, 3028)


In [17]:
# Plotting some graphs of vascular-activity
import plotly.express as px
from scipy.signal import savgol_filter

x, y = time_vector, vascular_diameter[0]

px.scatter(x=x, y=y, title="Blood-Vessel by Time").show()

yhat = savgol_filter(y, 51, 3) # window size 51, polynomial order 3
px.scatter(x=x, y=yhat, title="Blood-Vessel by Time [Smoothed]", color_discrete_sequence=["orange"]).show()


print_vascu_values_dist(limit=5)

Values Dist for each Blooad Vessel


In [ ]:
# TODO more

In [20]:
def print_neuro_values_dist(limit=5):
    assert limit < neuronal_dff.shape[0]
    import plotly.figure_factory as ff

    # Group data together
    hist_data = [neuronal_dff[i] for i in range(limit)]

    labels = [f"Neuro_{i}" for i in range(limit)]

    # Create distplot with custom bin_size
    fig = ff.create_distplot(hist_data, labels, bin_size=.2)
    print("Values Dist for each Neuronl")
    fig.show()
    
def print_vascu_values_dist(limit=5):
    assert limit < vascular_diameter.shape[0]
    import plotly.figure_factory as ff

    # Group data together
    hist_data = [vascular_diameter[i] for i in range(limit)]

    labels = [f"Vessel_{i}" for i in range(limit)]

    # Create distplot with custom bin_size
    fig = ff.create_distplot(hist_data, labels, bin_size=.2)
    print("Values Dist for each Blooad Vessel")
    fig.show()

In [21]:
# TODO more

In [22]:
# Some conclusions: (TODO add anything we notice)
#  - 50 different neurons, against 426 different vessels
#  - 3028 time units for each
#  - that's not a lot of data to work with :( But we'll manage